# Análisis de Perfiles de Riesgo en Seguros Médicos

Objetivo: Determinar perfiles de alto riesgo que estén pagando un coste menor de póliza

## 1. Carga de Librerías y Datos

In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report, confusion_matrix

import warnings
warnings.filterwarnings('ignore')

plt.style.use('seaborn-v0_8-darkgrid')
sns.set_palette('husl')

In [2]:
df = pd.read_csv('medical_insurance.csv')
print(f"Datos cargados: {df.shape[0]} registros, {df.shape[1]} columnas")
df.head()

Datos cargados: 100000 registros, 54 columnas


person_id  age     sex   region urban_rural   income     education  \
0      75722   52  Female    North    Suburban  22700.0     Doctorate   
1      80185   79  Female    North       Urban  12800.0         No HS   
2      19865   68    Male    North       Rural  40700.0            HS   
3      76700   15    Male    North    Suburban  15600.0  Some College   
4      92992   53    Male  Central    Suburban  89600.0     Doctorate   

  marital_status employment_status  household_size  ...  liver_disease  \
0        Married           Retired               3  ...              0   
1        Married          Employed               3  ...              0   
2        Married           Retired               5  ...              0   
3        Married     Self-employed               5  ...              0   
4        Married     Self-employed               2  ...              0   

   arthritis mental_health proc_imaging_count  proc_surgery_count  \
0          1             0                  1                   0   
1          1             1                  0                   0   
2          0             1                  1                   0   
3          0             0                  1                   0   
4          1             0                  2                   0   

   proc_physio_count  proc_consult_count  proc_lab_count  is_high_risk  \
0                  2                   0               1             0   
1                  1                   0               1             1   
2                  2                   1               0             1   
3                  0                   1               0             0   
4                  1                   1               0             1   

   had_major_procedure  
0                    0  
1                    0  
2                    0  
3                    0  
4                    0  

[5 rows x 54 columns]

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 100000 entries, 0 to 99999
Data columns (total 54 columns):
 #   Column                       Non-Null Count   Dtype  
---  ------                       --------------   -----  
 0   person_id                    100000 non-null  int64  
 1   age                          100000 non-null  int64  
 2   sex                          100000 non-null  object 
 3   region                       100000 non-null  object 
 4   urban_rural                  100000 non-null  object 
 5   income                       100000 non-null  float64
 6   education                    100000 non-null  object 
 7   marital_status               100000 non-null  object 
 8   employment_status            100000 non-null  object 
 9   household_size               100000 non-null  int64  
 10  dependents                   100000 non-null  int64  
 11  bmi                          100000 non-null  float64
 12  smoker                       100000 non-null  object 
 13  

## 2. Procedimiento: Análisis Exploratorio

### 2.1. Perfil Sociodemográfico de la Muestra

In [4]:
fig = make_subplots(
    rows=2, cols=3,
    subplot_titles=('Distribución por Edad', 'Distribución por Sexo', 'Distribución por Región',
                   'Distribución por Estado Civil', 'Distribución por Educación', 'Distribución por Zona'),
    specs=[[{'type': 'histogram'}, {'type': 'bar'}, {'type': 'bar'}],
           [{'type': 'bar'}, {'type': 'bar'}, {'type': 'bar'}]]
)

fig.add_trace(go.Histogram(x=df['age'], name='Edad', marker_color='#636EFA'), row=1, col=1)

sex_counts = df['sex'].value_counts()
fig.add_trace(go.Bar(x=sex_counts.index, y=sex_counts.values, name='Sexo', marker_color='#EF553B'), row=1, col=2)

region_counts = df['region'].value_counts()
fig.add_trace(go.Bar(x=region_counts.index, y=region_counts.values, name='Región', marker_color='#00CC96'), row=1, col=3)

marital_counts = df['marital_status'].value_counts()
fig.add_trace(go.Bar(x=marital_counts.index, y=marital_counts.values, name='Estado Civil', marker_color='#AB63FA'), row=2, col=1)

edu_counts = df['education'].value_counts()
fig.add_trace(go.Bar(x=edu_counts.index, y=edu_counts.values, name='Educación', marker_color='#FFA15A'), row=2, col=2)

urban_counts = df['urban_rural'].value_counts()
fig.add_trace(go.Bar(x=urban_counts.index, y=urban_counts.values, name='Zona', marker_color='#19D3F3'), row=2, col=3)

fig.update_layout(height=700, showlegend=False, title_text="Perfil Sociodemográfico de la Muestra")
fig.show()

### 2.2. Distribución de Enfermedades

In [5]:
enfermedades = ['hypertension', 'diabetes', 'asthma', 'copd', 'cardiovascular_disease',
                'cancer_history', 'kidney_disease', 'liver_disease', 'arthritis', 'mental_health']

prevalencia = df[enfermedades].sum().sort_values(ascending=True)

fig = go.Figure()
fig.add_trace(go.Bar(
    y=prevalencia.index,
    x=prevalencia.values,
    orientation='h',
    marker=dict(color=prevalencia.values, colorscale='Reds')
))

fig.update_layout(
    title='Prevalencia de Enfermedades Crónicas en la Muestra',
    xaxis_title='Número de Casos',
    yaxis_title='Enfermedad',
    height=500
)
fig.show()

### 2.3. Promedio de Lifestyle por Tipo de Plan

In [6]:
lifestyle_vars = ['bmi', 'age', 'income', 'household_size', 'dependents']

lifestyle_por_plan = df.groupby('plan_type')[lifestyle_vars].mean().round(2)

fig = go.Figure()

for var in lifestyle_vars:
    fig.add_trace(go.Bar(
        name=var,
        x=lifestyle_por_plan.index,
        y=lifestyle_por_plan[var],
        text=lifestyle_por_plan[var],
        textposition='auto'
    ))

fig.update_layout(
    title='Promedio de Variables Lifestyle por Tipo de Plan',
    xaxis_title='Tipo de Plan',
    yaxis_title='Valor Promedio',
    barmode='group',
    height=500
)
fig.show()

lifestyle_por_plan

bmi    age    income  household_size  dependents
plan_type                                                    
EPO        27.02  47.68  50164.50            2.44        0.91
HMO        26.98  47.45  49718.16            2.43        0.89
POS        26.96  47.64  49972.82            2.43        0.89
PPO        27.00  47.48  49860.58            2.43        0.90

### 2.4. Gasto e Ingreso Medio Real por Plan

In [7]:
df['ingreso_aseguradora'] = df['annual_premium'] + (df['monthly_premium'] * 12)
df['margen'] = df['ingreso_aseguradora'] - df['total_claims_paid']

analisis_plan = df.groupby('plan_type').agg({
    'total_claims_paid': 'mean',
    'ingreso_aseguradora': 'mean',
    'margen': 'mean',
    'person_id': 'count'
}).round(2)

analisis_plan.columns = ['Gasto Medio (Claims)', 'Ingreso Medio', 'Margen Medio', 'N° Clientes']

fig = make_subplots(
    rows=1, cols=2,
    subplot_titles=('Gasto vs Ingreso por Plan', 'Margen por Plan'),
    specs=[[{'type': 'bar'}, {'type': 'bar'}]]
)

fig.add_trace(
    go.Bar(name='Gasto (Claims)', x=analisis_plan.index, y=analisis_plan['Gasto Medio (Claims)'], marker_color='#EF553B'),
    row=1, col=1
)
fig.add_trace(
    go.Bar(name='Ingreso', x=analisis_plan.index, y=analisis_plan['Ingreso Medio'], marker_color='#00CC96'),
    row=1, col=1
)

fig.add_trace(
    go.Bar(x=analisis_plan.index, y=analisis_plan['Margen Medio'], 
           marker_color=analisis_plan['Margen Medio'].apply(lambda x: '#00CC96' if x > 0 else '#EF553B'),
           showlegend=False),
    row=1, col=2
)

fig.update_layout(height=400, title_text='Análisis Financiero por Tipo de Plan')
fig.show()

analisis_plan

Gasto Medio (Claims)  Ingreso Medio  Margen Medio  N° Clientes
plan_type                                                                
EPO                     1366.30        1162.53       -203.77        15121
HMO                     1387.85        1163.55       -224.30        34723
POS                     1373.86        1165.12       -208.73        14989
PPO                     1374.73        1166.42       -208.31        35167

### 2.5. Perfil Sociodemográfico por Tipo de Seguro

In [8]:
perfil_por_plan = df.groupby('plan_type').agg({
    'age': 'mean',
    'income': 'mean',
    'bmi': 'mean',
    'household_size': 'mean',
    'chronic_count': 'mean',
    'is_high_risk': lambda x: (x.sum() / len(x)) * 100
}).round(2)

perfil_por_plan.columns = ['Edad Media', 'Ingreso Medio', 'BMI Medio', 'Tamaño Hogar', 'Enfermedades Crónicas', '% Alto Riesgo']

fig = go.Figure()

for col in perfil_por_plan.columns:
    fig.add_trace(go.Scatter(
        x=perfil_por_plan.index,
        y=perfil_por_plan[col],
        mode='lines+markers',
        name=col,
        line=dict(width=3)
    ))

fig.update_layout(
    title='Perfil Sociodemográfico por Tipo de Plan (Normalizado)',
    xaxis_title='Tipo de Plan',
    yaxis_title='Valor',
    height=500,
    hovermode='x unified'
)
fig.show()

perfil_por_plan

Edad Media  Ingreso Medio  BMI Medio  Tamaño Hogar  \
plan_type                                                       
EPO             47.68       50164.50      27.02          2.44   
HMO             47.45       49718.16      26.98          2.43   
POS             47.64       49972.82      26.96          2.43   
PPO             47.48       49860.58      27.00          2.43   

           Enfermedades Crónicas  % Alto Riesgo  
plan_type                                        
EPO                         0.73          37.30  
HMO                         0.72          36.86  
POS                         0.71          36.39  
PPO                         0.73          36.65

### 2.6. Perfil Sociodemográfico por Network Tier

In [25]:
perfil_por_tier = df.groupby('network_tier').agg({
    'person_id': 'count',
}).round(2)

perfil_por_tier.columns = ['Cuenta de Clientes']

fig = go.Figure(data=[
    go.Bar(name=col, x=perfil_por_tier.index, y=perfil_por_tier[col])
    for col in perfil_por_tier.columns
])

fig.update_layout(
    title='Número de Clientes por Network Tier',
    xaxis_title='Network Tier',
    yaxis_title='Total',
    barmode='group',
    height=500
)
fig.show()

perfil_por_tier

Cuenta de Clientes
network_tier                    
Bronze                     29932
Gold                       19882
Platinum                   10009
Silver                     40177

### 2.7. Número de Reclamaciones por Network Tier

In [ ]:
reclamaciones_tier = df.groupby('network_tier').agg({
    'claims_count': 'mean',
    'total_claims_paid': 'mean',
    'avg_claim_amount': 'mean',
    'person_id': 'count'
}).round(2)

reclamaciones_tier.columns = ['Reclamaciones por Cliente', 'Gasto por Cliente ($)', 'Monto Medio por Reclamación ($)', 'N° Clientes']

fig = make_subplots(
    rows=1, cols=3,
    subplot_titles=('Reclamaciones por Cliente', 'Gasto Medio por Cliente ($)', 'Monto por Reclamación ($)')
)

fig.add_trace(
    go.Bar(x=reclamaciones_tier.index, y=reclamaciones_tier['Reclamaciones por Cliente'], 
           marker_color='#636EFA', name='Reclamaciones',
           text=reclamaciones_tier['Reclamaciones por Cliente'],
           textposition='auto'),
    row=1, col=1
)

fig.add_trace(
    go.Bar(x=reclamaciones_tier.index, y=reclamaciones_tier['Gasto por Cliente ($)'], 
           marker_color='#EF553B', name='Gasto',
           text=reclamaciones_tier['Gasto por Cliente ($)'],
           textposition='auto'),
    row=1, col=2
)

fig.add_trace(
    go.Bar(x=reclamaciones_tier.index, y=reclamaciones_tier['Monto Medio por Reclamación ($)'], 
           marker_color='#00CC96', name='Monto',
           text=reclamaciones_tier['Monto Medio por Reclamación ($)'],
           textposition='auto'),
    row=1, col=3   
)

fig.update_layout(height=400, showlegend=False, title_text='Análisis de Reclamaciones por Network Tier (Ponderado por Cliente)')
fig.show()

print("\nMétricas Ponderadas por Network Tier:")
print("=" * 80)
print(reclamaciones_tier)
print("=" * 80)

## 3. Dashboard: Visualizaciones Clave

### 3.1. Enfermedades más Presentes por Tipo de Plan

In [11]:
enfermedades_cols = ['hypertension', 'diabetes', 'asthma', 'copd', 'cardiovascular_disease',
                     'cancer_history', 'kidney_disease', 'liver_disease', 'arthritis', 'mental_health']

enf_por_plan = df.groupby('plan_type')[enfermedades_cols].sum()

fig = go.Figure()

for plan in enf_por_plan.index:
    fig.add_trace(go.Bar(
        name=plan,
        x=enfermedades_cols,
        y=enf_por_plan.loc[plan],
        text=enf_por_plan.loc[plan],
        textposition='auto'
    ))

fig.update_layout(
    title='Distribución de Enfermedades por Tipo de Plan',
    xaxis_title='Enfermedad',
    yaxis_title='Número de Casos',
    barmode='group',
    height=500,
    xaxis_tickangle=-45
)
fig.show()

In [ ]:
enf_por_plan_pct = df.groupby('plan_type')[enfermedades_cols].mean() * 100

fig = go.Figure(data=go.Heatmap(
    z=enf_por_plan_pct.values,
    x=enf_por_plan_pct.columns,
    y=enf_por_plan_pct.index,
    colorscale='RdYlBu_r',
    text=enf_por_plan_pct.values.round(1),
    texttemplate='%{text}%',
    textfont={"size": 10}
))

fig.update_layout(
    title='Porcentaje de Prevalencia de Enfermedades por Tipo de Plan',
    xaxis_title='Enfermedad',
    yaxis_title='Tipo de Plan',
    height=400,
    xaxis_tickangle=-45
)
fig.show()

### 3.2. Perfil de Lifestyle por Tipo de Enfermedad

In [12]:
df['tiene_enfermedad_cronica'] = df['chronic_count'] > 0

lifestyle_numeric = ['bmi', 'age', 'income']

comparacion = df.groupby('tiene_enfermedad_cronica')[lifestyle_numeric].mean()

fig = make_subplots(
    rows=1, cols=3,
    subplot_titles=('BMI', 'Edad', 'Ingreso')
)

fig.add_trace(
    go.Bar(x=['Sin Enfermedad', 'Con Enfermedad'], 
           y=[comparacion.loc[False, 'bmi'], comparacion.loc[True, 'bmi']],
           marker_color=['#00CC96', '#EF553B']),
    row=1, col=1
)

fig.add_trace(
    go.Bar(x=['Sin Enfermedad', 'Con Enfermedad'], 
           y=[comparacion.loc[False, 'age'], comparacion.loc[True, 'age']],
           marker_color=['#00CC96', '#EF553B']),
    row=1, col=2
)

fig.add_trace(
    go.Bar(x=['Sin Enfermedad', 'Con Enfermedad'], 
           y=[comparacion.loc[False, 'income'], comparacion.loc[True, 'income']],
           marker_color=['#00CC96', '#EF553B']),
    row=1, col=3
)

fig.update_layout(height=400, showlegend=False, title_text='Perfil de Lifestyle: Con vs Sin Enfermedades Crónicas')
fig.show()

In [13]:
enf_individual = {}
for enf in ['hypertension', 'diabetes', 'cardiovascular_disease']:
    enf_individual[enf] = df.groupby(enf)['bmi'].mean()

fig = go.Figure()

for enf, data in enf_individual.items():
    fig.add_trace(go.Bar(
        name=enf,
        x=['Sin ' + enf, 'Con ' + enf],
        y=[data[0], data[1]],
        text=[f'{data[0]:.1f}', f'{data[1]:.1f}'],
        textposition='auto'
    ))

fig.update_layout(
    title='BMI Promedio por Enfermedad Específica',
    xaxis_title='Estado',
    yaxis_title='BMI Promedio',
    barmode='group',
    height=400
)
fig.show()

### 3.3. Relación entre Cambios de Póliza y Total Pagado

In [14]:
df['ha_cambiado_poliza'] = df['policy_changes_last_2yrs'] > 0

fig = px.box(
    df, 
    x='ha_cambiado_poliza', 
    y='total_claims_paid',
    color='ha_cambiado_poliza',
    labels={'ha_cambiado_poliza': 'Ha Cambiado Póliza', 'total_claims_paid': 'Total Pagado por Aseguradora'},
    title='Relación entre Cambios de Póliza y Total Pagado por la Aseguradora'
)
fig.update_layout(height=500)
fig.show()

In [15]:
cambios_analisis = df.groupby('policy_changes_last_2yrs').agg({
    'total_claims_paid': 'mean',
    'annual_medical_cost': 'mean',
    'person_id': 'count'
}).round(2)

cambios_analisis.columns = ['Total Pagado Medio', 'Coste Médico Anual Medio', 'Número de Clientes']

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=cambios_analisis.index,
    y=cambios_analisis['Total Pagado Medio'],
    mode='lines+markers',
    name='Total Pagado',
    line=dict(width=3, color='#EF553B')
))

fig.add_trace(go.Scatter(
    x=cambios_analisis.index,
    y=cambios_analisis['Coste Médico Anual Medio'],
    mode='lines+markers',
    name='Coste Médico',
    line=dict(width=3, color='#636EFA')
))

fig.update_layout(
    title='Impacto del Número de Cambios de Póliza en Costes',
    xaxis_title='Número de Cambios de Póliza (últimos 2 años)',
    yaxis_title='Monto ($)',
    height=500,
    hovermode='x unified'
)
fig.show()

cambios_analisis

Total Pagado Medio  Coste Médico Anual Medio  \
policy_changes_last_2yrs                                                 
0                                    1378.50                   3008.51   
1                                    1369.28                   3031.38   
2                                    1228.09                   2864.70   

                          Número de Clientes  
policy_changes_last_2yrs                      
0                                      95047  
1                                       4837  
2                                        116

## 4. Modelo Predictivo: Clasificación de Alto Riesgo

### 4.1. Preparación de Datos

In [16]:
features_demographics = ['age', 'income', 'household_size', 'dependents']
features_lifestyle = ['bmi']

features = features_demographics + features_lifestyle

X = df[features].copy()
y = df['is_high_risk'].copy()

X = X.fillna(X.median())

print(f"Features seleccionadas: {features}")
print(f"Shape de X: {X.shape}")
print(f"Distribución de y: {y.value_counts()}")

Features seleccionadas: ['age', 'income', 'household_size', 'dependents', 'bmi']
Shape de X: (100000, 5)
Distribución de y: is_high_risk
0    63219
1    36781
Name: count, dtype: int64


### 4.2. División y Escalado

In [17]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, stratify=y)

scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)

print(f"Train set: {X_train.shape[0]} registros")
print(f"Test set: {X_test.shape[0]} registros")

Train set: 80000 registros
Test set: 20000 registros


### 4.3. Entrenamiento del Modelo

In [18]:
rf_model = RandomForestClassifier(n_estimators=100, random_state=42, max_depth=10, min_samples_split=20)
rf_model.fit(X_train_scaled, y_train)

y_pred = rf_model.predict(X_test_scaled)

print("=" * 60)
print("RESULTADOS DEL MODELO")
print("=" * 60)
print(classification_report(y_test, y_pred, target_names=['Bajo Riesgo', 'Alto Riesgo']))

RESULTADOS DEL MODELO
              precision    recall  f1-score   support

 Bajo Riesgo       0.85      0.83      0.84     12644
 Alto Riesgo       0.71      0.74      0.73      7356

    accuracy                           0.80     20000
   macro avg       0.78      0.79      0.78     20000
weighted avg       0.80      0.80      0.80     20000



### 4.4. Dashboard de Coeficientes (Importancia de Features)

In [19]:
importancias = pd.DataFrame({
    'Feature': features,
    'Importancia': rf_model.feature_importances_
}).sort_values('Importancia', ascending=True)

fig = go.Figure()

fig.add_trace(go.Bar(
    y=importancias['Feature'],
    x=importancias['Importancia'],
    orientation='h',
    marker=dict(
        color=importancias['Importancia'],
        colorscale='Viridis',
        colorbar=dict(title="Importancia")
    ),
    text=importancias['Importancia'].round(3),
    textposition='auto'
))

fig.update_layout(
    title='Importancia de Variables en la Predicción de Alto Riesgo',
    xaxis_title='Importancia (Feature Importance)',
    yaxis_title='Variable',
    height=400,
    showlegend=False
)
fig.show()

importancias.sort_values('Importancia', ascending=False)

Feature  Importancia
0             age     0.919215
4             bmi     0.056278
1          income     0.018210
2  household_size     0.003455
3      dependents     0.002843

### 4.5. Matriz de Confusión

In [20]:
cm = confusion_matrix(y_test, y_pred)

fig = go.Figure(data=go.Heatmap(
    z=cm,
    x=['Predicho: Bajo Riesgo', 'Predicho: Alto Riesgo'],
    y=['Real: Bajo Riesgo', 'Real: Alto Riesgo'],
    text=cm,
    texttemplate='%{text}',
    colorscale='Blues',
    showscale=True
))

fig.update_layout(
    title='Matriz de Confusión',
    xaxis_title='Predicción',
    yaxis_title='Valor Real',
    height=400
)
fig.show()

## 5. Análisis Final: Perfiles de Alto Riesgo con Bajo Coste de Póliza

In [21]:
df['prima_total_anual'] = df['annual_premium'] + (df['monthly_premium'] * 12)

umbral_prima_baja = df['prima_total_anual'].quantile(0.33)

alto_riesgo_prima_baja = df[(df['is_high_risk'] == 1) & (df['prima_total_anual'] <= umbral_prima_baja)]

print(f"Total de clientes de alto riesgo: {df['is_high_risk'].sum()}")
print(f"Clientes de alto riesgo con prima baja (≤ ${umbral_prima_baja:.2f}): {len(alto_riesgo_prima_baja)}")
print(f"Porcentaje: {(len(alto_riesgo_prima_baja) / df['is_high_risk'].sum() * 100):.2f}%")

Total de clientes de alto riesgo: 36781
Clientes de alto riesgo con prima baja (≤ $767.96): 7067
Porcentaje: 19.21%


In [22]:
perfil_problema = alto_riesgo_prima_baja.describe()[['age', 'bmi', 'income', 'chronic_count', 
                                                       'total_claims_paid', 'prima_total_anual']]
perfil_problema.loc['median'] = alto_riesgo_prima_baja[['age', 'bmi', 'income', 'chronic_count', 
                                                          'total_claims_paid', 'prima_total_anual']].median()

perfil_problema.round(2)

age      bmi     income  chronic_count  total_claims_paid  \
count   7067.00  7067.00    7067.00        7067.00            7067.00   
mean      60.67    27.33   51339.03           1.09             476.08   
std       12.69     5.17   48868.59           0.77             432.42   
min       14.00    12.00    2000.00           0.00               0.00   
25%       52.00    23.70   21600.00           1.00               0.00   
50%       60.00    27.40   36700.00           1.00             457.68   
75%       69.00    31.00   63900.00           2.00             771.03   
max      100.00    50.10  631900.00           4.00            2205.36   
median    60.00    27.40   36700.00           1.00             457.68   

        prima_total_anual  
count             7067.00  
mean               656.87  
std                 73.33  
min                435.38  
25%                604.32  
50%                665.97  
75%                717.60  
max                767.94  
median             665.97

In [23]:
fig = px.scatter(
    df,
    x='prima_total_anual',
    y='total_claims_paid',
    color='is_high_risk',
    labels={
        'prima_total_anual': 'Prima Total Anual ($)',
        'total_claims_paid': 'Total Pagado por Aseguradora ($)',
        'is_high_risk': 'Alto Riesgo'
    },
    title='Relación entre Prima Pagada y Reclamaciones: Identificación de Perfiles Problemáticos',
    opacity=0.6,
    color_discrete_map={0: '#00CC96', 1: '#EF553B'}
)

fig.add_vline(x=umbral_prima_baja, line_dash="dash", line_color="red", 
              annotation_text="Umbral Prima Baja", annotation_position="top")

fig.update_layout(height=600)
fig.show()

In [24]:
distribucion_planes = alto_riesgo_prima_baja['plan_type'].value_counts()

fig = go.Figure(data=[go.Pie(
    labels=distribucion_planes.index,
    values=distribucion_planes.values,
    hole=0.3
)])

fig.update_layout(
    title='Distribución de Tipos de Plan en Perfiles de Alto Riesgo con Prima Baja',
    height=400
)
fig.show()

## 6. Análisis de Perfiles Críticos: Prima Baja + Gasto Alto & Bajo Riesgo + Gasto Alto

### 6.1. Identificación de Perfiles Críticos

In [ ]:
umbral_prima_baja = df['prima_total_anual'].quantile(0.25)
umbral_gasto_alto = df['total_claims_paid'].quantile(0.75)

perfil_1 = df[(df['prima_total_anual'] <= umbral_prima_baja) & (df['total_claims_paid'] >= umbral_gasto_alto)]
perfil_2 = df[(df['is_high_risk'] == 0) & (df['total_claims_paid'] >= umbral_gasto_alto)]

print("=" * 80)
print("PERFILES CRÍTICOS IDENTIFICADOS")
print("=" * 80)
print(f"\n1. PERFIL: Prima Baja + Gasto Alto")
print(f"   - Prima ≤ ${umbral_prima_baja:.2f}")
print(f"   - Gasto ≥ ${umbral_gasto_alto:.2f}")
print(f"   - Total clientes: {len(perfil_1)} ({len(perfil_1)/len(df)*100:.2f}%)")
print(f"   - Pérdida media por cliente: ${(perfil_1['total_claims_paid'].mean() - perfil_1['prima_total_anual'].mean()):.2f}")

print(f"\n2. PERFIL: Bajo Riesgo + Gasto Alto")
print(f"   - Clasificado como Bajo Riesgo (is_high_risk = 0)")
print(f"   - Gasto ≥ ${umbral_gasto_alto:.2f}")
print(f"   - Total clientes: {len(perfil_2)} ({len(perfil_2)/len(df)*100:.2f}%)")
print(f"   - Gasto medio: ${perfil_2['total_claims_paid'].mean():.2f}")
print("=" * 80)

### 6.2. Visualización de Perfiles Críticos en el Espacio Prima-Gasto

In [ ]:
df['perfil_critico'] = 'Normal'
df.loc[(df['prima_total_anual'] <= umbral_prima_baja) & (df['total_claims_paid'] >= umbral_gasto_alto), 'perfil_critico'] = 'Prima Baja + Gasto Alto'
df.loc[(df['is_high_risk'] == 0) & (df['total_claims_paid'] >= umbral_gasto_alto), 'perfil_critico'] = 'Bajo Riesgo + Gasto Alto'

colores = {
    'Normal': '#00CC96',
    'Prima Baja + Gasto Alto': '#EF553B',
    'Bajo Riesgo + Gasto Alto': '#FFA15A'
}

fig = px.scatter(
    df,
    x='prima_total_anual',
    y='total_claims_paid',
    color='perfil_critico',
    color_discrete_map=colores,
    opacity=0.5,
    labels={
        'prima_total_anual': 'Prima Total Anual ($)',
        'total_claims_paid': 'Total Pagado por Aseguradora ($)',
        'perfil_critico': 'Perfil'
    },
    title='Identificación de Perfiles Críticos: Prima vs Gasto'
)

fig.add_hline(y=umbral_gasto_alto, line_dash="dash", line_color="red", 
              annotation_text="Umbral Gasto Alto", annotation_position="right")
fig.add_vline(x=umbral_prima_baja, line_dash="dash", line_color="blue", 
              annotation_text="Umbral Prima Baja", annotation_position="top")

fig.update_layout(height=600)
fig.show()

### 6.3. Comparación Demográfica de Perfiles Críticos

In [ ]:
comparacion_perfiles = pd.DataFrame({
    'Prima Baja + Gasto Alto': perfil_1[['age', 'bmi', 'income', 'chronic_count']].mean(),
    'Bajo Riesgo + Gasto Alto': perfil_2[['age', 'bmi', 'income', 'chronic_count']].mean(),
    'Promedio General': df[['age', 'bmi', 'income', 'chronic_count']].mean()
}).round(2)

fig = go.Figure()

for col in comparacion_perfiles.columns:
    fig.add_trace(go.Bar(
        name=col,
        x=comparacion_perfiles.index,
        y=comparacion_perfiles[col],
        text=comparacion_perfiles[col],
        textposition='auto'
    ))

fig.update_layout(
    title='Comparación Demográfica: Perfiles Críticos vs Promedio General',
    xaxis_title='Variable',
    yaxis_title='Valor Promedio',
    barmode='group',
    height=500
)
fig.show()

comparacion_perfiles.T

### 6.4. Prevalencia de Enfermedades en Perfiles Críticos

In [ ]:
enfermedades_cols = ['hypertension', 'diabetes', 'asthma', 'copd', 'cardiovascular_disease',
                     'cancer_history', 'kidney_disease', 'liver_disease', 'arthritis', 'mental_health']

enf_perfil1 = (perfil_1[enfermedades_cols].sum() / len(perfil_1) * 100).sort_values(ascending=False)
enf_perfil2 = (perfil_2[enfermedades_cols].sum() / len(perfil_2) * 100).sort_values(ascending=False)
enf_general = (df[enfermedades_cols].sum() / len(df) * 100).sort_values(ascending=False)

fig = go.Figure()

fig.add_trace(go.Bar(
    name='Prima Baja + Gasto Alto',
    x=enfermedades_cols,
    y=[enf_perfil1[e] for e in enfermedades_cols],
    text=[f'{enf_perfil1[e]:.1f}%' for e in enfermedades_cols],
    textposition='auto',
    marker_color='#EF553B'
))

fig.add_trace(go.Bar(
    name='Bajo Riesgo + Gasto Alto',
    x=enfermedades_cols,
    y=[enf_perfil2[e] for e in enfermedades_cols],
    text=[f'{enf_perfil2[e]:.1f}%' for e in enfermedades_cols],
    textposition='auto',
    marker_color='#FFA15A'
))

fig.add_trace(go.Bar(
    name='Promedio General',
    x=enfermedades_cols,
    y=[enf_general[e] for e in enfermedades_cols],
    text=[f'{enf_general[e]:.1f}%' for e in enfermedades_cols],
    textposition='auto',
    marker_color='#00CC96'
))

fig.update_layout(
    title='Prevalencia de Enfermedades: Perfiles Críticos vs Población General',
    xaxis_title='Enfermedad',
    yaxis_title='Prevalencia (%)',
    barmode='group',
    height=500,
    xaxis_tickangle=-45
)
fig.show()

### 6.5. Distribución de Planes en Perfiles Críticos

In [ ]:
fig = make_subplots(
    rows=1, cols=2,
    subplot_titles=('Prima Baja + Gasto Alto', 'Bajo Riesgo + Gasto Alto'),
    specs=[[{'type': 'pie'}, {'type': 'pie'}]]
)

plan_perfil1 = perfil_1['plan_type'].value_counts()
fig.add_trace(
    go.Pie(labels=plan_perfil1.index, values=plan_perfil1.values, name='Perfil 1'),
    row=1, col=1
)

plan_perfil2 = perfil_2['plan_type'].value_counts()
fig.add_trace(
    go.Pie(labels=plan_perfil2.index, values=plan_perfil2.values, name='Perfil 2'),
    row=1, col=2
)

fig.update_layout(
    title_text='Distribución de Tipos de Plan en Perfiles Críticos',
    height=400
)
fig.show()

In [ ]:
tier_perfil1 = perfil_1['network_tier'].value_counts()
tier_perfil2 = perfil_2['network_tier'].value_counts()
tier_general = df['network_tier'].value_counts()

tier_perfil1_pct = (tier_perfil1 / len(perfil_1) * 100).reindex(['Bronze', 'Silver', 'Gold', 'Platinum'], fill_value=0)
tier_perfil2_pct = (tier_perfil2 / len(perfil_2) * 100).reindex(['Bronze', 'Silver', 'Gold', 'Platinum'], fill_value=0)
tier_general_pct = (tier_general / len(df) * 100).reindex(['Bronze', 'Silver', 'Gold', 'Platinum'], fill_value=0)

fig = go.Figure()

fig.add_trace(go.Bar(
    name='Prima Baja + Gasto Alto',
    x=['Bronze', 'Silver', 'Gold', 'Platinum'],
    y=tier_perfil1_pct,
    text=[f'{v:.1f}%' for v in tier_perfil1_pct],
    textposition='auto',
    marker_color='#EF553B'
))

fig.add_trace(go.Bar(
    name='Bajo Riesgo + Gasto Alto',
    x=['Bronze', 'Silver', 'Gold', 'Platinum'],
    y=tier_perfil2_pct,
    text=[f'{v:.1f}%' for v in tier_perfil2_pct],
    textposition='auto',
    marker_color='#FFA15A'
))

fig.add_trace(go.Bar(
    name='Promedio General',
    x=['Bronze', 'Silver', 'Gold', 'Platinum'],
    y=tier_general_pct,
    text=[f'{v:.1f}%' for v in tier_general_pct],
    textposition='auto',
    marker_color='#00CC96'
))

fig.update_layout(
    title='Distribución de Network Tier: Perfiles Críticos vs Población General',
    xaxis_title='Network Tier',
    yaxis_title='Porcentaje (%)',
    barmode='group',
    height=450
)
fig.show()

### 6.6. Utilización de Servicios Médicos en Perfiles Críticos

In [ ]:
servicios = ['visits_last_year', 'hospitalizations_last_3yrs', 'medication_count', 
             'proc_imaging_count', 'proc_surgery_count', 'proc_consult_count']

util_perfil1 = perfil_1[servicios].mean()
util_perfil2 = perfil_2[servicios].mean()
util_general = df[servicios].mean()

comparacion_servicios = pd.DataFrame({
    'Prima Baja + Gasto Alto': util_perfil1,
    'Bajo Riesgo + Gasto Alto': util_perfil2,
    'Promedio General': util_general
}).round(2)

fig = go.Figure()

for col in comparacion_servicios.columns:
    fig.add_trace(go.Bar(
        name=col,
        x=comparacion_servicios.index,
        y=comparacion_servicios[col],
        text=comparacion_servicios[col],
        textposition='auto'
    ))

fig.update_layout(
    title='Utilización de Servicios Médicos: Perfiles Críticos vs Población General',
    xaxis_title='Tipo de Servicio',
    yaxis_title='Cantidad Promedio',
    barmode='group',
    height=500,
    xaxis_tickangle=-45
)
fig.show()

comparacion_servicios.T

### 6.7. Resumen Financiero: Impacto de Perfiles Críticos

In [ ]:
resumen_financiero = pd.DataFrame({
    'Perfil': ['Prima Baja + Gasto Alto', 'Bajo Riesgo + Gasto Alto', 'Población General'],
    'N° Clientes': [len(perfil_1), len(perfil_2), len(df)],
    'Prima Media ($)': [
        perfil_1['prima_total_anual'].mean(),
        perfil_2['prima_total_anual'].mean(),
        df['prima_total_anual'].mean()
    ],
    'Gasto Medio ($)': [
        perfil_1['total_claims_paid'].mean(),
        perfil_2['total_claims_paid'].mean(),
        df['total_claims_paid'].mean()
    ],
    'Margen Medio ($)': [
        perfil_1['margen'].mean(),
        perfil_2['margen'].mean(),
        df['margen'].mean()
    ],
    'Pérdida Total ($)': [
        perfil_1['margen'].sum(),
        perfil_2['margen'].sum(),
        df['margen'].sum()
    ],
    '% Alto Riesgo': [
        (perfil_1['is_high_risk'].sum() / len(perfil_1) * 100),
        (perfil_2['is_high_risk'].sum() / len(perfil_2) * 100),
        (df['is_high_risk'].sum() / len(df) * 100)
    ]
}).round(2)

resumen_financiero['% del Total'] = (resumen_financiero['N° Clientes'] / len(df) * 100).round(2)

print("=" * 100)
print("RESUMEN FINANCIERO: IMPACTO DE PERFILES CRÍTICOS")
print("=" * 100)
print(resumen_financiero.to_string(index=False))
print("=" * 100)

fig = make_subplots(
    rows=1, cols=2,
    subplot_titles=('Margen Medio por Perfil', 'Pérdida Total por Perfil'),
    specs=[[{'type': 'bar'}, {'type': 'bar'}]]
)

fig.add_trace(
    go.Bar(
        x=resumen_financiero['Perfil'],
        y=resumen_financiero['Margen Medio ($)'],
        text=resumen_financiero['Margen Medio ($)'],
        textposition='auto',
        marker_color=['#EF553B', '#FFA15A', '#00CC96'],
        name='Margen Medio'
    ),
    row=1, col=1
)

fig.add_trace(
    go.Bar(
        x=resumen_financiero['Perfil'],
        y=resumen_financiero['Pérdida Total ($)'],
        text=resumen_financiero['Pérdida Total ($)'].apply(lambda x: f'${x/1e6:.1f}M'),
        textposition='auto',
        marker_color=['#EF553B', '#FFA15A', '#00CC96'],
        name='Pérdida Total'
    ),
    row=1, col=2
)

fig.update_layout(height=400, showlegend=False, title_text='Impacto Financiero de Perfiles Críticos')
fig.show()